In [1]:
import sys
sys.path.insert(0,'..')
import folium
#import pandas as pd
#folium.initialize_notebook()

In [2]:
#Standard OSM
map_osm = folium.Map(location=[45.5236, -122.6750])
map_osm

In [3]:
stamen = folium.Map(location=[45.5236, -122.6750], tiles='Stamen Toner',
                    zoom_start=13)
stamen

In [4]:
mt_hood = folium.Map(location=[45.372, -121.6972], zoom_start=12,
                     tiles='Stamen Terrain')
folium.Marker([45.3288, -121.6625], popup='Mt. Hood Meadows').add_to(mt_hood)
folium.Marker([45.3311, -121.7113], popup='Timberline Lodge', icon=folium.Icon()).add_to(mt_hood)
mt_hood

In [5]:
portland = folium.Map(location=[45.5236, -122.6750], tiles='Stamen Toner',
                      zoom_start=13)
folium.Marker([45.5244, -122.6699], popup='The Waterfront').add_to(portland)
folium.CircleMarker([45.5215, -122.6261], radius=500,
                    popup='Laurelhurst Park', color='#3186cc',
                    fill_color='#3186cc').add_to(portland)
portland

In [6]:
latlng = folium.Map(location=[46.1991, -122.1889], tiles='Stamen Terrain',
                    zoom_start=13)
folium.LatLngPopup().add_to(latlng)
latlng

In [7]:
waypoints = folium.Map(location=[46.8527, -121.7649], tiles='Stamen Terrain',
                       zoom_start=13)
folium.Marker([46.8354, -121.7325], popup='Camp Muir').add_to(waypoints)
folium.ClickForMarker().add_to(waypoints)
waypoints

In [8]:
polygons = folium.Map(location=[45.5236, -122.6750], zoom_start=13)

folium.RegularPolygonMarker([45.5012, -122.6655], popup='Ross Island Bridge',
                        fill_color='#132b5e', number_of_sides=3, radius=10).add_to(polygons)
folium.RegularPolygonMarker([45.5132, -122.6708], popup='Hawthorne Bridge',
                        fill_color='#45647d', number_of_sides=4, radius=10).add_to(polygons)
folium.RegularPolygonMarker([45.5275, -122.6692], popup='Steel Bridge',
                        fill_color='#769d96', number_of_sides=6, radius=10).add_to(polygons)
folium.RegularPolygonMarker([45.5318, -122.6745], popup='Broadway Bridge',
                        fill_color='#769d96', number_of_sides=8, radius=10).add_to(polygons)
polygons

In [9]:
import vincent
import pandas as pd
import numpy as np

NOAA_46041 = pd.read_csv(r'NOAA_46041.csv', index_col=3,
                         parse_dates=True)
NOAA_46050 = pd.read_csv(r'NOAA_46050_WS.csv', index_col=3,
                         parse_dates=True)
NOAA_46243 = pd.read_csv(r'NOAA_46243.csv', index_col=3,
                         parse_dates=True)

NOAA_46041 = NOAA_46041.dropna()

#Binned wind speeds for NOAA 46050
bins = range(0, 13, 1)
cuts = pd.cut(NOAA_46050['wind_speed_cwind (m/s)'], bins)
ws_binned = pd.Series(
    np.histogram(NOAA_46050['wind_speed_cwind (m/s)'], bins=bins)[0],
    index=bins[:-1])

#NOAA 46401 Wave Period
vis1 = vincent.Line(NOAA_46041['dominant_wave_period (s)'],
                    width=400, height=200)
vis1.axis_titles(x='Time', y='Dominant Wave Period (s)')
vis1.to_json('vis1.json')

#NOAA 46050 Binned Wind Speed
vis2 = vincent.Bar(ws_binned, width=400, height=200)
vis2.axis_titles(x='Wind Speed (m/s)', y='# of Obs')
vis2.to_json('vis2.json')

#NOAA 46243 Wave Height
vis3 = vincent.Area(NOAA_46243['significant_wave_height (m)'],
                    width=400, height=200)
vis3.axis_titles(x='Time', y='Significant Wave Height (m)')
vis3.to_json('vis3.json')

#Map all buoys
buoy_map = folium.Map(location=[46.3014, -123.7390], zoom_start=7,
                      tiles='Stamen Terrain')

popup1 = folium.Popup(max_width=800,
                     ).add_child(folium.Vega(vis1, width=500, height=250))
folium.RegularPolygonMarker([47.3489, -124.708],
                            fill_color='#43d9de',
                            radius=12,
                            popup=popup1).add_to(buoy_map)

popup2 = folium.Popup(max_width=800,
                     ).add_child(folium.Vega(vis2, width=500, height=250))
folium.RegularPolygonMarker([44.639, -124.5339],
                            fill_color='#43d9de',
                            radius=12,
                            popup=popup2).add_to(buoy_map)

popup3 = folium.Popup(max_width=800,
                     ).add_child(folium.Vega(vis3, width=500, height=250))
folium.RegularPolygonMarker([46.216, -124.1280],
                            fill_color='#43d9de',
                            radius=12,
                            popup=popup3).add_to(buoy_map)

buoy_map

In [10]:
state_geo = r'us-states.json'
state_unemployment = r'US_Unemployment_Oct2012.csv'

state_data = pd.read_csv(state_unemployment)

#Let Folium determine the scale
states = folium.Map(location=[48, -102], zoom_start=3)
states.choropleth(geo_path=state_geo, data=state_data,
                columns=['State', 'Unemployment'],
                key_on='feature.id',
                fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Unemployment Rate (%)')

states

/home/journois/anaconda3/envs/test/lib/python3.5/site-packages/ipykernel/__main__.py:12: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [11]:
states2 = folium.Map(location=[48, -102], zoom_start=3)
states2.choropleth(geo_path=state_geo, data=state_data,
                 columns=['State', 'Unemployment'],
                 threshold_scale=[5, 6, 7, 8, 9, 10],
                 key_on='feature.id',
                 fill_color='BuPu', fill_opacity=0.7, line_opacity=0.5,
                 legend_name='Unemployment Rate (%)',
                 reset=True)
states2

In [12]:
county_data = r'us_county_data.csv'
county_geo = r'us_counties_20m_topo.json'

df = pd.read_csv(county_data, na_values=[' '])


colorscale = folium.colormap.linear.YlOrRd.scale(0,50e3)
employed_series = df.set_index('FIPS_Code')['Employed_2011']

def style_function(feature):
    employed = employed_series.get(int(feature['id'][-5:]),None)
    return {
        'fillOpacity' : 0.5,
        'weight' : 0,
        'fillColor' : '#black' if employed is None else colorscale(employed)
    }

#Number of employed with auto scale
map_1 = folium.Map(location=[48, -102], tiles='cartodbpositron',
                   zoom_start=3)

folium.TopoJson(open(county_geo),
                'objects.us_counties_20m',
                style_function=style_function).add_to(map_1)

map_1

In [13]:
colorscale = folium.colormap.linear.YlGnBu.scale(0,30)
employed_series = df.set_index('FIPS_Code')['Unemployment_rate_2011']

def style_function(feature):
    employed = employed_series.get(int(feature['id'][-5:]),None)
    return {
        'fillOpacity' : 0.5,
        'weight' : 0,
        'fillColor' : '#black' if employed is None else colorscale(employed)
    }

#Number of employed with auto scale
map_2 = folium.Map(location=[48, -102], tiles='cartodbpositron',
                   zoom_start=3)

folium.TopoJson(open(county_geo),
                'objects.us_counties_20m',
                style_function=style_function).add_to(map_2)

map_2

In [14]:
colorscale = folium.colormap.linear.PuRd.scale(0,100000)
employed_series = df.set_index('FIPS_Code')['Median_Household_Income_2011'].dropna()

def style_function(feature):
    employed = employed_series.get(int(feature['id'][-5:]),None)
    return {
        'fillOpacity' : 0.5,
        'weight' : 0,
        'fillColor' : '#black' if employed is None else colorscale(employed)
    }

#Number of employed with auto scale
map_3 = folium.Map(location=[48, -102], tiles='cartodbpositron',
                   zoom_start=3)

folium.TopoJson(open(county_geo),
                'objects.us_counties_20m',
                style_function=style_function).add_to(map_3)

map_3